In [ ]:
##Python venv: search_agent_poc

In [3]:
##This module will take the serialized dictionary got out of PDF Parsing ann try to extract
##Semantic Knowldge like identifying 
## 1.Important Objects/Entities
## 2.Deduplicate Entities
## 3.Extracting Relations
## 4.Extract the main Ideas/Topics around Each Page
## 5.Link the different topics via diffrent entities/Objects
## 6.Break down the document by pages instead of Chunks .
## 7.If a page does not fit a chunk then chunk them extract information and then deduplicate the information across
## the page.

#Next Steps:
## 5.Try to Seggregate the BigPDF on Sections.
## 8.Try To Find Common Objects or ideas that link these sections.
## 9.Try 

In [9]:
import numpy as np
import numpy as np
import matplotlib.pyplot as plt
import os
import json
import pickle
import ollama
import chromadb
from chromadb.config import DEFAULT_TENANT, DEFAULT_DATABASE, Settings
import pandas as pd
#from langchain_community.vectorstores import Chroma

In [10]:
import pickle
import pandas as pd
#rag_test_input_path='/home/matrix4284/MY_GEN_AI_PROJECTS/RAG/GraphRAG/graphrag-local-ollama/ragtest/input/'+file_name
import os
# importing shutil module
import shutil

from langchain_community.chat_models import ChatOllama

from langchain_community.embeddings import HuggingFaceEmbeddings

from langchain_community.embeddings.sentence_transformer import (
    SentenceTransformerEmbeddings,
)

#from sentence_transformers import SentenceTransformer
#embeddings = SentenceTransformer("all-MiniLM-L6-v2")

from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain_community.vectorstores import Chroma

import json
import operator
from typing import Annotated, Sequence, TypedDict

from langchain import hub
from langchain.prompts import PromptTemplate
from langchain_community.vectorstores import Chroma
from langchain_core.messages import BaseMessage, FunctionMessage
from langchain_core.output_parsers import StrOutputParser
from langchain_core.pydantic_v1 import BaseModel, Field
from langchain_core.runnables import RunnablePassthrough
from langchain_community.chat_models import ChatOllama
from langchain_core.output_parsers import JsonOutputParser
import json
import operator
from typing import Annotated, Sequence, TypedDict

from langchain import hub
from langchain.prompts import PromptTemplate
from langchain_community.vectorstores import Chroma
from langchain_core.messages import BaseMessage, FunctionMessage
from langchain_core.output_parsers import StrOutputParser
from langchain_core.pydantic_v1 import BaseModel, Field
from langchain_core.runnables import RunnablePassthrough
from langchain_community.chat_models import ChatOllama
from langchain_core.output_parsers import JsonOutputParser
from langchain_core.output_parsers import StrOutputParser
from langchain.output_parsers import XMLOutputParser

In [11]:
import networkx as nx
from pyvis.network import Network

In [12]:
graph_output_dir="./graph_output_networkx/"
single_entity_file="nodes_with_single_ocurence.csv"
input_graph="graph_phase3_with_multi_occurence_nodes_entity_desc_embeddings.graphml"
output_graph_graphml="graph_phase4_with_relationship_desc_embeddings.graphml"
#output_graph_gml="graph_phase4_with_relationship_desc_embeddings.gml"
pdf_enrichment_output_dir = '../pdf_enrichment/pdf_enriched_output/'  
pdf_enrichment_output_file = 'pdf_enriched_content_dict_phase5_extract_highligts_478_final.pickle'

In [13]:
G=nx.read_graphml(graph_output_dir+input_graph)

In [14]:
graph_output_dir='./graph_output_networkx/'
multi_entity_file='nodes_with_multi_ocurence.csv'
multi_df=pd.read_csv(graph_output_dir+multi_entity_file)
multi_df=multi_df.reset_index(drop=True).reset_index().dropna()
multi_df['index']

0          0
1          1
2          2
3          3
4          4
        ... 
4346    4346
4347    4347
4348    4348
4349    4349
4350    4350
Name: index, Length: 4340, dtype: int64

In [15]:
# Load data (deserialized data) into serilaizable list of of data#####
###This acts as the source for the Graph Building ######
import pickle
with open(pdf_enrichment_output_dir+pdf_enrichment_output_file, 'rb') as handle:
    document_dict_deserialized = pickle.load(handle)

In [16]:
doc_len=len(document_dict_deserialized)

In [17]:
document_dict_deserialized[5]['relationships'][0]

{'source_entity': '"volumes"',
 'description': 'are used to store data for a pod',
 'destination_entity': '"Pod specification/contents"'}

In [25]:
def graph_enrichment_with_relation(triples):
    if (triples['source_entity'] is not None) and (triples['destination_entity'] is not None):
        G.add_edge(triples['source_entity'],triples['destination_entity'],description=triples['description'])
    return G

def chroma_collection_populator_source_entity(collection_name,docs_lst):
    idx=0
    for item in docs_lst:
        print('Source Entity:')
        print(item['source_entity'])
        print('index:')
        print(idx)
        try:
            if len(item['source_entity'])>0 or item['source_entity'] is not None:
           
                response = ollama.embeddings(model="mxbai-embed-large", prompt=item['source_entity'])
                embedding = response["embedding"]
                print(np.array(embedding))
    
                collection_name.add(
                    ids=[str(idx)],
                    embeddings=[embedding],
                    documents=[item['source_entity']]
                    )
            else:
                print("Destination entity does not exist")
        except:
            print("source_entity is of None Type")
    
        idx=idx+1
        
    return collection_name

def chroma_collection_populator_destination_entity(collection_name,docs_lst):
    idx=0
    for item in docs_lst:
        print('Destination Entity:')
        print(item['destination_entity'])
        print('index:')
        print(idx)
        try:
            if len(item['destination_entity'])>0 or item['destination_entity'] is not None:
            
                response = ollama.embeddings(model="mxbai-embed-large", prompt=item['destination_entity'])
                embedding = response["embedding"]
                print(np.array(embedding))
    
                collection_name.add(
                    ids=[str(idx)],
                    embeddings=[embedding],
                    documents=[item['destination_entity']]
                    )          
            else:
                print("Destination entity does not exist")
        except:
            print("There was None type in entities")
            
        idx=idx+1
        
    return collection_name


def chroma_collection_populator_description(collection_name,docs_lst):
    idx=0
    for item in docs_lst:
        print('Descriprion Of Relation Entity:')
        print(item['description'])
        print('index:')
        print(idx)
        try:
            if len(item['description'])>0 or item['description'] is not None:
            
                response = ollama.embeddings(model="mxbai-embed-large", prompt=item['description'])
                embedding = response["embedding"]
                print(np.array(embedding))
    
                collection_name.add(
                    ids=[str(idx)],
                    embeddings=[embedding],
                    documents=[item['description']]
                    )
            else:
                print("Decsription is not present")
        except:
            print("The description is of None Type")
    
        idx=idx+1
        
    return collection_name


def chroma_collection_populator_description_with_entities(collection_name,docs_lst):
    idx=0
    for item in docs_lst:
        print('Descriprion Of Relation Entity:')
        print(item['description'])
        print('index:')
        print(idx)
        try:
            if len(item['description'])>0 or item['description'] is not None:
            
                response = ollama.embeddings(model="mxbai-embed-large", prompt=item['source_entity']+' '+item['description']+ ' ' +item['destination_entity'])
                embedding = response["embedding"]
                print(np.array(embedding))
    
                collection_name.add(
                    ids=[str(idx)],
                    embeddings=[embedding],
                    documents=[item['source_entity']+' '+item['description']+ ' ' +item['destination_entity']]
                    )
            else:
                print("Decsription is not present")
        except:
            print("The description is of None Type")
    
        idx=idx+1
        
    return collection_name

def query_collection(collection_name,query,n):
    query = query
    # generate an embedding for the prompt and retrieve the most relevant doc
    response = ollama.embeddings(
      prompt=query,
      model="mxbai-embed-large"
    )
    results = collection_name.query(
      query_embeddings=[response["embedding"]],
      n_results=n
    )
    return results

#entity_idx=0
def embedder(index,text,collection):
    print(text)
    response = ollama.embeddings(model="mxbai-embed-large", prompt=text)
    embedding = response["embedding"]
    #print(np.array(embedding))
    try:
        collection.add(
            ids=[str(index)],
            embeddings=[embedding],
            documents=[text]
          )
    except:
          'COULD NOT LOAD INTO VECTOR DATABASE'
    #entity_idx=entity_idx+1
    return embedding

In [26]:
#nx.write_graphml_lxml(G, graph_output_dir+output_graph_graphml)
#nx.write_gml(G, graph_output_dir+output_graph_gml)

In [27]:
client = chromadb.PersistentClient(
    path="./Kubernetes_in_Action_ChromaDB",
    settings=Settings(),
    tenant=DEFAULT_TENANT,
    database=DEFAULT_DATABASE,
)

In [28]:
#Define all the collection corresponding to the source_entity,destination_entity & Relationship Description

collection_source_entity = client.delete_collection(name="source_entity")
collection_source_entity = client.get_or_create_collection(name="source_entity")

collection_destination_entity = client.delete_collection(name="destination_entity")
collection_destination_entity = client.get_or_create_collection(name="destination_entity")

collection_description = client.delete_collection(name="description")
collection_description = client.get_or_create_collection(name="description")

collection_relation_entities = client.delete_collection(name="description_with_entities")
collection_relation_entities = client.get_or_create_collection(name="description_with_entities")

In [29]:
for idx in range(0,doc_len):
    if 'relationships' in document_dict_deserialized[idx]:
        relationlst_per_page=document_dict_deserialized[idx]['relationships']
        
        collection_relation_entities=chroma_collection_populator_description_with_entities(collection_relation_entities,relationlst_per_page)
        #collection_destination_entity=chroma_collection_populator_destination_entity(collection_destination_entity,relationlst_per_page)
        #collection_description=chroma_collection_populator_description(collection_description,relationlst_per_page)
        for triples in document_dict_deserialized[idx]['relationships']:
            print(triples)
            graph_enrichment_with_relation(triples)
    else:
        print('relationship key not got')

Descriprion Of Relation Entity:
manages
index:
0
[ 0.02745984 -0.18872252  0.6163699  ... -0.40240717  0.15850647
  0.64150727]
Descriprion Of Relation Entity:
allocates
index:
1
[-0.22950718 -0.03518049  0.61875701 ... -0.62505454 -0.45270324
  0.14153069]
Descriprion Of Relation Entity:
manages
index:
2
[-0.43228948 -0.40847     0.45176658 ... -0.50268012 -0.26370567
 -0.16497985]
Descriprion Of Relation Entity:
orchestrates
index:
3
[ 0.06703278 -0.01608037 -0.37908161 ... -0.16761558  1.11755228
  0.44354361]
Descriprion Of Relation Entity:
runs
index:
4
[-0.13026965  0.18104514  0.17589857 ...  0.37576029  0.7807886
  0.27189407]
Descriprion Of Relation Entity:
manages
index:
5
[-0.07115463  0.13009661 -0.1213652  ... -0.00412014  0.40049776
  0.36767253]
Descriprion Of Relation Entity:
manages
index:
6
[-0.26113224 -0.39178401  0.83213615 ... -0.84802401  0.13231133
  0.05721921]
Descriprion Of Relation Entity:
manages
index:
7


Insert of existing embedding ID: 0
Add of existing embedding ID: 0
Insert of existing embedding ID: 1
Add of existing embedding ID: 1


[-0.15678492 -0.43249875  0.70778561 ... -1.12375975  0.16142941
  0.03917371]
{'source_entity': '"Network namespace"', 'description': 'manages', 'destination_entity': '"Linux namespaces"'}
{'source_entity': '"Network namespace"', 'description': 'allocates', 'destination_entity': '"Port space"'}
{'source_entity': '"UTS namespace"', 'description': 'manages', 'destination_entity': '"Linux namespaces"'}
{'source_entity': '"Kubernetes"', 'description': 'orchestrates', 'destination_entity': '"Pods"'}
{'source_entity': '"Docker"', 'description': 'runs', 'destination_entity': '"Containers"'}
{'source_entity': '"Kubernetes"', 'description': 'manages', 'destination_entity': '"Volume"'}
{'source_entity': '"PID namespace"', 'description': 'manages', 'destination_entity': '"Linux namespaces"'}
{'source_entity': '"IPC namespace"', 'description': 'manages', 'destination_entity': '"Linux namespaces"'}
Descriprion Of Relation Entity:
manages
index:
0
[ 0.16109693  0.00924915 -0.39055559 ... -0.1135193

Insert of existing embedding ID: 2
Add of existing embedding ID: 2
Insert of existing embedding ID: 3
Add of existing embedding ID: 3


[-0.48582828 -0.07028246  0.26066512 ...  0.40885457  0.24653915
  0.09318759]
Descriprion Of Relation Entity:
uses
index:
3
[-0.32347563  0.59615111  0.38802224 ...  0.01422107  0.64611942
 -0.21929519]
Descriprion Of Relation Entity:
hosts
index:
4


...

[ 0.10833284 -0.35255161 -0.06616139 ... -0.12436293  0.60706925
  0.39423448]
Descriprion Of Relation Entity:
runs a single-node cluster
index:
6
[ 0.1657784   0.44921267 -0.27664363 ...  0.15907082  0.65875751
  0.08098088]
Descriprion Of Relation Entity:
stores configuration for kubectl
index:
7
[ 0.06904884 -0.12173896  0.07609713 ... -0.31547973  0.73691154
  0.13868974]
Descriprion Of Relation Entity:
defines the API version for Kubernetes
index:
8


Insert of existing embedding ID: 8
Add of existing embedding ID: 8
Insert of existing embedding ID: 9
Add of existing embedding ID: 9


[ 0.18527934  0.53014457 -0.21065919 ... -0.03129886  0.17643172
  0.03381882]
Descriprion Of Relation Entity:
specifies the URL of the server
index:
9
[-0.10292448  0.38121298 -0.21679911 ...  0.02080107 -0.31337923
  0.56157494]
Descriprion Of Relation Entity:
lists all available clusters
index:
10


Insert of existing embedding ID: 10
Add of existing embedding ID: 10
Insert of existing embedding ID: 11
Add of existing embedding ID: 11
Insert of existing embedding ID: 12
Add of existing embedding ID: 12


[-0.27933836  0.71506399 -0.0174369  ... -0.19962211  1.08349836
  0.39785987]
Descriprion Of Relation Entity:
manages user authentication for Kubernetes
index:
11
[ 4.88467097e-01 -5.04944474e-04 -2.31203407e-01 ... -4.18469578e-01
  7.02733874e-01  2.01837897e-01]
Descriprion Of Relation Entity:
specifies the path to the certificate authority file
index:
12
[ 0.05287679 -0.48400801  0.74271744 ... -0.07607741  0.38902807
 -0.30694836]
{'source_entity': 'kubectl', 'description': 'uses to connect to a cluster', 'destination_entity': 'cluster'}
{'source_entity': 'KUBECONFIG environment variable', 'description': 'stores the path to the kubeconfig file', 'destination_entity': 'kubeconfig file'}
{'source_entity': 'kubectl', 'description': 'displays information about multiple clusters', 'destination_entity': 'multiple clusters'}
{'source_entity': 'current-context', 'description': 'sets the current context for kubectl', 'destination_entity': 'kubectl'}
{'source_entity': 'namespace', 'descrip

In [30]:
for idx in range(0,doc_len):
    if 'relationships' in document_dict_deserialized[idx]:
        relationlst_per_page=document_dict_deserialized[idx]['relationships']
        collection_source_entity=chroma_collection_populator_source_entity(collection_source_entity,relationlst_per_page)
        collection_destination_entity=chroma_collection_populator_destination_entity(collection_destination_entity,relationlst_per_page)
        collection_description=chroma_collection_populator_description(collection_description,relationlst_per_page)
        #collection_destination_entity=chroma_collection_populator_destination_entity(collection_destination_entity,relationlst_per_page)
        #collection_description=chroma_collection_populator_description(collection_description,relationlst_per_page)
        #for triples in document_dict_deserialized[idx]['relationships']:
        #    print(triples)
        #    #graph_enrichment_with_relation(triples)
    else:
        print('relationship key not got')

Source Entity:
"Network namespace"
index:
0
[ 0.03643603 -0.1220261   0.49763709 ... -0.19431731 -0.06395335
  0.47481644]
Source Entity:
"Network namespace"
index:
1
[ 0.03643603 -0.1220261   0.49763709 ... -0.19431731 -0.06395335
  0.47481644]
Source Entity:
"UTS namespace"
index:
2
[-0.5538131  -0.62068003  0.25384986 ... -0.48529518 -0.45940587
 -0.63288128]
Source Entity:
"Kubernetes"
index:
3
[ 0.36920792  0.0898497  -0.7526114  ...  0.20026262  0.54431111
 -0.05273924]
Source Entity:
"Docker"
index:
4
[ 0.30695844 -0.01954547 -0.31244689 ...  0.30542162  0.11295849
  0.18550995]
Source Entity:
"Kubernetes"
index:
5
[ 0.36920792  0.0898497  -0.7526114  ...  0.20026262  0.54431111
 -0.05273924]
Source Entity:
"PID namespace"
index:
6
[-0.38619903 -0.55171573  0.70367879 ... -0.8615371   0.05946776
 -0.34228057]
Source Entity:
"IPC namespace"
index:
7
[-0.20750102 -0.56936228  0.42907217 ... -1.15884054  0.06809257
 -0.27797198]
Destination Entity:
"Linux namespaces"
index:
0
[ 0.2

Insert of existing embedding ID: 0
Add of existing embedding ID: 0


[ 0.09887224 -0.40605623 -0.72587013 ... -0.72712594  0.092021
  0.49461365]
Descriprion Of Relation Entity:
manages
index:
7
[ 0.09887224 -0.40605623 -0.72587013 ... -0.72712594  0.092021
  0.49461365]
Source Entity:
"Kubernetes"
index:
0
[ 0.36920792  0.0898497  -0.7526114  ...  0.20026262  0.54431111
 -0.05273924]
Source Entity:
"Kubernetes"
index:
1


Insert of existing embedding ID: 1
Add of existing embedding ID: 1
Insert of existing embedding ID: 2
Add of existing embedding ID: 2


[ 0.36920792  0.0898497  -0.7526114  ...  0.20026262  0.54431111
 -0.05273924]
Source Entity:
"Container 1"
index:
2
[-0.22845298 -0.19183622  0.48098314 ...  0.03509964  0.55547357
 -0.56956112]
Source Entity:
"Container 2"
index:
3


...

[ 0.2778331   0.5773527  -0.39242646 ...  0.35327363  0.70417941
  0.3041487 ]
Descriprion Of Relation Entity:
stores configuration for kubectl
index:
7
[-0.13213971 -0.49562645 -0.25647765 ... -0.44907033  0.69209254
  0.34412929]
Descriprion Of Relation Entity:
defines the API version for Kubernetes
index:
8
[ 0.29656172  0.4776628  -0.27452266 ...  0.03203431 -0.13875829
  0.36151379]
Descriprion Of Relation Entity:
specifies the URL of the server
index:
9


Add of existing embedding ID: 9
Insert of existing embedding ID: 9
Add of existing embedding ID: 10
Insert of existing embedding ID: 10


[-0.04627938  0.05348292 -0.04049651 ... -0.40535873 -0.56021798
  0.71358782]
Descriprion Of Relation Entity:
lists all available clusters
index:
10
[-0.25898442  0.39937493  0.19520818 ... -0.24403121  1.01443672
  0.31067669]
Descriprion Of Relation Entity:
manages user authentication for Kubernetes
index:
11


Add of existing embedding ID: 11
Insert of existing embedding ID: 11
Add of existing embedding ID: 12
Insert of existing embedding ID: 12


[ 0.57259864 -0.04603385 -0.21836537 ... -0.28537497  0.57323456
  0.25118059]
Descriprion Of Relation Entity:
specifies the path to the certificate authority file
index:
12
[ 0.10416786 -0.23356166  0.48174056 ... -0.43674845  0.07288928
  0.41636214]


In [31]:
query_collection(collection_source_entity,"how to test whether a pod is runing",3)

{'ids': [['23', '3', '5']],
 'distances': [[204.09279694965682, 287.9953842311855, 287.9953842311855]],
 'metadatas': [[None, None, None]],
 'embeddings': None,
 'documents': [['pod selector', '"Kubernetes"', '"Kubernetes"']],
 'uris': None,
 'data': None}

In [32]:
query_collection(collection_relation_entities,"how to test whether a pod is runing",10)

{'ids': [['19', '22', '15', '16', '14', '3', '23', '20', '13', '9']],
 'distances': [[206.01926848193278,
   216.1423406591376,
   229.15219895421507,
   238.8038892674614,
   244.34102764373378,
   244.49692289388912,
   252.133225015091,
   252.41182779267385,
   254.54271815489435,
   256.13326972568154]],
 'metadatas': [[None, None, None, None, None, None, None, None, None, None]],
 'embeddings': None,
 'documents': [['"nodeName" specifies the name of the node on which a pod is running "Pod specification/contents"',
   'service has a specific pod selector pod selector',
   '"Spec" specifies the configuration of a pod "Pod specification/contents"',
   '"name" represents the name of a pod or container "Pod specification/contents"',
   '"serviceAccount" represents the service account used by a pod "Pod specification/contents"',
   '"Kubernetes" orchestrates "Pods"',
   'pod selector defines which pods are part of the service service',
   '"terminationMessagePath" specifies the path to

In [33]:

query_collection(collection_destination_entity,"resource type",3)

{'ids': [['19', '13', '14']],
 'distances': [[212.52599943924628, 212.52599943924628, 212.52599943924628]],
 'metadatas': [[None, None, None]],
 'embeddings': None,
 'documents': [['"Pod specification/contents"',
   '"Pod specification/contents"',
   '"Pod specification/contents"']],
 'uris': None,
 'data': None}

In [34]:

nx.write_graphml_lxml(G, graph_output_dir+output_graph_graphml)

In [ ]:
###Visualization of the Graph

In [35]:
####The main contents of Kubernets In Action book is contained from page 87 to 565####
####Thats why we will only take the sliced portion i.e. from page 87 to 565 of the pdf dictionary list#####
nt = Network('800px', '2000px',notebook=True,cdn_resources='remote')
# populates the nodes and edges data structures
nt.from_nx(G)
nt.toggle_physics(True)
nt.show('graph_phase4_with_relationship_desc_embeddings.html')
#nt.show_buttons(filter_=['physics'])
nt.save('graph_phase4_with_relationship_desc_embeddings.html')
#nt.write_html('graph_stage1.html')

KeyboardInterrupt: 